In [1]:
import numpy as np
from ipywidgets import interactive_output, VBox, HBox


**Learning goals:**

- Be able to explain what an ***eigenvector*** and an ***eigenvalue*** of a matrix are. 
- Be able to explain how you can see *one* eigenvector-eigenvalue pair in the long term behavior of a discrete-time linear model. 


**Recall the black bear population model:** 

**Assumptions:** 
- The population is split into two types of bears: juveniles ($J$) and adults ($A$). 
- Each year, on average, $42\%$ of adults give birth to a cub. 
- Each year, $24\%$ of juveniles reach adulthood. 
- Each year, $15\%$ of adult bears die, and $29\%$ of juvenile bears die. 

**Resulting model:** 

$$ \begin{pmatrix} J_{t+1} \\ A_{t+1} \end{pmatrix} = \begin{pmatrix} 0.47 J_t + 0.42 A_t \\ 0.24 J_t + 0.85 A_t \end{pmatrix} = \begin{bmatrix} 0.47 & 0.42 \\ 0.24 & 0.85 \end{bmatrix} \begin{pmatrix} J_t \\ A_t \end{pmatrix}$$


In [2]:
def matrix_interactive():
    M = matrix(RDF, [[0.47, 0.42], [0.24, 0.85]])
    show(r"M = " + latex(M))

    years = 30
    solution = [vector((500.0, 250.0))]
    for t in range(years + 1):
        solution.append(M * solution[-1])

    @interact(t=slider(0, years, 1, label="$t$"))
    def update(t):
        show(LatexExpr(r"t = %d" % (t,)))
        show(LatexExpr(r"\text{Current state: } \begin{bmatrix} %.1f \\ %.1f \end{bmatrix}" % tuple(solution[t])))
        show(LatexExpr(r"\text{Next state: } \begin{bmatrix} %.1f \\ %.1f \end{bmatrix}" % tuple(solution[t + 1])))

matrix_interactive()


M = \left(\begin{array}{rr}
0.47 & 0.42 \\
0.24 & 0.85
\end{array}\right)

Interactive function <function matrix_interactive.<locals>.update at 0x7f407c5a53a0> with 1 widget
  t: Transf…

In [3]:
def blackbear_interactive_single():
    xmax, ymax = (850, 850)
    M = matrix(RDF, [[0.47, 0.42], [0.24, 0.85]])

    years = 30
    solution = [vector((500, 250))]
    for t in range(years):
        solution.append(M * solution[-1])
    solution = np.array(solution, dtype=float)

    labeltext = r"\begin{bmatrix} J_{%d} \\ A_{%d} \end{bmatrix} = \begin{bmatrix} %.1f \\ %.1f \end{bmatrix}"

    @interact(t=slider(0, years, 1, label="$t$"))
    def update(t):
        p = list_plot(solution[:t+1], color="blue")
        p.show(xmin=0, ymin=0, xmax=850, ymax=850, aspect_ratio=1, axes_labels=("$J$", "$A$"))
        show(LatexExpr(labeltext % (t, t, *solution[t])))

blackbear_interactive_single()

Interactive function <function blackbear_interactive_single.<locals>.update at 0x7f3e574a64c0> with 1 widget
 …

In [4]:
def blackbear_interactive_many():
    xmax, ymax = (850, 850)
    M = matrix(RDF, [[0.47, 0.42], [0.24, 0.85]])
    evector = sorted(M.eigenvectors_right())[-1][1][0]
    length = vector((xmax, ymax)).norm()

    years = 30
    t_range = srange(20)
    solutions = {
        "blue":      [vector((500, 250))], 
        "darkorange":[vector((500,  50))], 
        "red":       [vector((150, 500))], 
        "darkgreen": [vector(( 50, 700))], 
    }
    for solution in solutions.values():
        for t in range(years):
            solution.append(M * solution[-1])
    solutions = {color: np.array(solution, dtype=float) for color, solution in solutions.items()}

    controls = {color: slider(0, years, 1, label=color) for color in solutions}
    controls["show_eigenline"] = checkbox(False, label="Show “trend”")
    @interact(**controls)
    def update(**controls):
        p = Graphics()
        for color, solution in solutions.items():
            t = controls[color]
            p += list_plot(solution[:t+1], color=color)
            p += list_plot(solution[:t+1], color=color, plotjoined=True)
        if controls["show_eigenline"]:
            p += line([evector * -length, evector * length], color="magenta", thickness=3, alpha=0.6)
        p.show(xmin=0, ymin=0, xmax=850, ymax=850, aspect_ratio=1, axes_labels=("$J$", "$A$"))

blackbear_interactive_many()


Interactive function <function blackbear_interactive_many.<locals>.update at 0x7f3e55117280> with 5 widgets
  …

In [5]:
def blackbear_interactive_vectors():
    xmax, ymax = (850, 850)
    M = matrix(RDF, [[0.47, 0.42], [0.24, 0.85]])

    years = 30
    t_range = srange(20)
    solution = [vector((500, 250))]
    for t in range(years + 1):
        solution.append(M * solution[-1])
    labeltext = r"\begin{bmatrix} J_{%d} \\ A_{%d} \end{bmatrix} = \begin{bmatrix} %.1f \\ %.1f \end{bmatrix}"

    @interact(t=slider(0, years, 1, label="$t$"), 
              show_vectors=checkbox(False, label="Show arrows"), 
              just2=checkbox(False, label="Just current and next"))
    def update(t, show_vectors, just2):
        p = Graphics()
        if just2:
            p += plot(solution[t], color="blue")
            p += plot(solution[t+1], color="green")
        else:
            p += list_plot(solution[:t+1], color="blue")
            if show_vectors:
                p += plot(solution[t], color="blue")
        p.show(xmin=0, ymin=0, xmax=850, ymax=850, aspect_ratio=1, axes_labels=("$J$", "$A$"))
        show(LatexExpr(labeltext % (t, t, *solution[t])))

blackbear_interactive_vectors()


Interactive function <function blackbear_interactive_vectors.<locals>.update at 0x7f3e5404caf0> with 3 widgets…

So what we just said is, eventually 
$$ [ \text{the next state} ] = ( \text{some scalar} ) [ \text{the current state} ] $$


But also, remember, we have a function $f$ for which 
$$ [ \text{the next state} ] = f( [ \text{the current state} ] ) $$


So that means that, eventually, we must have 
$$ f( [ \text{the current state} ] ) = ( \text{some scalar} ) [ \text{the current state} ] $$


So what we just said is, eventually 
$$ [ \text{the next state} ] = ( \text{some scalar} ) [ \text{the current state} ] $$

<br>

But also, remember, we have a matrix $M$ for which 
$$ [ \text{the next state} ] = M [ \text{the current state} ] $$

<br>

So that means that, eventually, we must have 
$$ M [ \text{the current state} ]  = ( \text{some scalar} ) [ \text{the current state} ] $$


**Definition:** Given a linear function $f: \mathbb{R}^n \to \mathbb{R}^n$, an $n$-dimensional vector $\vec{v}$ is called an ***eigenvector*** for $f$ if $\vec{v} \neq 0$ and 
$$ f(\vec{v}) = \lambda \vec{v} $$
for some *scalar* $\lambda$. In this case, the scalar $\lambda$ is called the ***eigenvalue*** of $f$ corresponding to eigenvector $\vec{v}$. 

<br>
<br>
<br>
<br>
<br>
<br>
<br>
<br>
<br>


**Definition:** Given an $n \times n$ matrix $M$, an $n$-dimensional vector $\vec{v}$ is called an ***eigenvector*** for $M$ if $\vec{v} \neq 0$ and 
<span style="color:blue"><strong>$$ M \vec{v} = \lambda \vec{v} $$</strong></span>
for some *scalar* $\lambda$. In this case, the scalar $\lambda$ is called the ***eigenvalue*** of $M$ corresponding to eigenvector $\vec{v}$. 


Notes: 
- Here $M$ is a matrix, $\vec{v}$ is a vector, and $\lambda$ is a scalar. 
- This definition means that eigenvalues and eigenvectors always go together: for any <br>eigenvector of a matrix, there is a corresponding eigenvalue, and vice-versa. 
- That symbol $\lambda$ is the (lowercase) Greek letter “lambda”. The prefix “eigen” ends up being applied to *many* things in math and science, all ultimately coming from this definition. It is of German origin, and hence is pronounced as in “Einstein”. 


In [6]:
blackbear_interactive_vectors()

Interactive function <function blackbear_interactive_vectors.<locals>.update at 0x7f606b9978b0> with 3 widgets…

**Conclusions:**

1. **Definition:** Given an $n \times n$ matrix $M$, a vector $\vec{v}$ is called an ***eigenvector*** for $M$ with ***eigenvalue*** $\lambda$ if $\vec{v} \neq 0$ and 
$$ M \vec{v} = \lambda \vec{v} . $$

2. Eigenvalues and eigenvectors tell us something about the long term behavior of a discrete-time linear model. But there's a lot more to this story, so we'll have to wait for more details here... 
